In [7]:
import os
import random
import shutil
import numpy as np
from PIL import Image, ImageDraw, ImageFont
import albumentations as A
from tqdm.auto import tqdm
import cv2 # Потрібен для preprocess_for_classifier

# ---------------------------------
# 1. КОНФІГУРАЦІЯ
# ---------------------------------
print("--- Етап 1: Мега-конфігурація ---")

# --- Загальні налаштування ---
BASE_DIR = 'learning'
FONT_DIR = os.path.join(BASE_DIR, 'fonts')
VALID_FONT_DIR = os.path.join(BASE_DIR, 'fonts_valid') # Використовуємо окремі для валідації

# Кількість БАЗОВИХ зображень.
# Загальна кількість буде NUM_BASE_IMAGES * 2 (оскільки 50% чистих, 50% аугментованих)
# Наприклад, 55000 дасть 110,000 всього зображень для YOLO
NUM_BASE_IMAGES = 55000
TRAIN_SPLIT_RATIO = 0.7 # 70% на тренування, 30% на валідацію

# --- Параметри генерації чисел ---
SCENE_SIZE = (640, 640) # Стандартний розмір для YOLO
FONT_SIZES = [40, 50, 60, 70, 80]
MAX_DIGITS_IN_NUMBER = 5 # Генеруватимемо числа від 1 до 5 цифр

# --- Шляхи для YOLO (Object Detection) ---
YOLO_DIR = os.path.join(BASE_DIR, 'data_yolo_mega')
YOLO_TRAIN_IMG = os.path.join(YOLO_DIR, 'train', 'images')
YOLO_TRAIN_LBL = os.path.join(YOLO_DIR, 'train', 'labels')
YOLO_VALID_IMG = os.path.join(YOLO_DIR, 'valid', 'images')
YOLO_VALID_LBL = os.path.join(YOLO_DIR, 'valid', 'labels')

# --- Шляхи для КЛАСИФІКАТОРА (Classifier) ---
CLASSIFIER_DIR = os.path.join(BASE_DIR, 'data_classifier_mega')
CLASS_TRAIN_DIR = os.path.join(CLASSIFIER_DIR, 'train')
CLASS_VALID_DIR = os.path.join(CLASSIFIER_DIR, 'valid')

# ---------------------------------
# 2. ОЧИЩЕННЯ ТА СТВОРЕННЯ ДИРЕКТОРІЙ
# ---------------------------------
print("Очищення старих директорій...")
if os.path.exists(YOLO_DIR):
    shutil.rmtree(YOLO_DIR)
if os.path.exists(CLASSIFIER_DIR):
    shutil.rmtree(CLASSIFIER_DIR)

print("Створення нових директорій...")
# Створюємо шляхи для YOLO
for path in [YOLO_TRAIN_IMG, YOLO_TRAIN_LBL, YOLO_VALID_IMG, YOLO_VALID_LBL]:
    os.makedirs(path, exist_ok=True)

# Створюємо шляхи для Класифікатора (10 класів 0-9)
for c in list(range(10)):
    os.makedirs(os.path.join(CLASS_TRAIN_DIR, str(c)), exist_ok=True)
    os.makedirs(os.path.join(CLASS_VALID_DIR, str(c)), exist_ok=True)

print("Структуру директорій створено.")

# ---------------------------------
# 3. ДОПОМІЖНІ ФУНКЦІЇ (З ОБОХ ФАЙЛІВ)
# ---------------------------------

def get_font_files(directory):
    try:
        files = [os.path.join(directory, f) for f in os.listdir(directory) if f.endswith('.ttf')]
        if not files:
            print(f"Попередження: Директорія {directory} порожня.")
        return files
    except FileNotFoundError:
        print(f"Помилка: Директорія {directory} не знайдена.")
        return []

def create_number_block(number_str, font_path, font_size):
    """
    Створює "блок" з цифр і повертає зображення та bboxes [class, x1, y1, x2, y2]
    (Логіка з Data_Generation_Yolo.ipynb)
    """
    try:
        font = ImageFont.truetype(font_path, font_size)
    except IOError:
        font = ImageFont.load_default()

    bboxes = []
    images = []
    current_x = 0

    for char in number_str:
        bbox = font.getbbox(char)
        char_width = bbox[2] - bbox[0]
        char_height = bbox[3] - bbox[1]

        # Додаємо трохи "padding" навколо символу
        char_img = Image.new('L', (char_width + 4, font_size + 10), 0) # 'L' = grayscale
        draw = ImageDraw.Draw(char_img)
        draw.text((2 - bbox[0], 5 - bbox[1]), char, font=font, fill=255)

        x_min = current_x + 2
        y_min = 5
        x_max = x_min + char_width
        y_max = y_min + char_height

        bboxes.append([int(char), x_min, y_min, x_max, y_max]) # [class, x1, y1, x2, y2]
        images.append(char_img)
        current_x += char_img.width + random.randint(-5, 2) # Випадковий кернінг

    total_width = current_x
    block_height = font_size + 10
    if total_width <= 0 or block_height <= 0:
        return None, None

    block_img = Image.new('L', (total_width, block_height), 0)
    current_x = 0
    for img in images:
        block_img.paste(img, (current_x, 0))
        current_x += img.width + random.randint(-5, 2)

    return np.array(block_img), bboxes

def preprocess_for_classifier(image_crop_gray, target_size=(64, 64)):
    """
    Масштабує та центрує вирізану цифру у квадрат 64x64.
    (Логіка з Data_Generation_Classifier_v2.ipynb)
    """
    h, w = image_crop_gray.shape[:2]
    if h == 0 or w == 0: return None

    # Зберігаємо пропорції
    scale = min(target_size[0] / h, target_size[1] / w)
    new_w, new_h = int(w * scale), int(h * scale)
    if new_h <= 0 or new_w <= 0: return None

    resized_img = cv2.resize(image_crop_gray, (new_w, new_h), interpolation=cv2.INTER_AREA)

    # Додаємо чорні поля (padding)
    delta_w, delta_h = target_size[1] - new_w, target_size[0] - new_h
    top, bottom = delta_h // 2, delta_h - (delta_h // 2)
    left, right = delta_w // 2, delta_w - (delta_w // 2)

    final_canvas = cv2.copyMakeBorder(resized_img, top, bottom, left, right,
                                     cv2.BORDER_CONSTANT, value=[0, 0, 0])
    return final_canvas

# ---------------------------------
# 4. ПАЙПЛАЙНИ АУГМЕНТАЦІЙ
# ---------------------------------

def get_transforms(is_augmented=False):
    """
    Повертає пайплайни для "блоку" та "сцени"
    """
    if not is_augmented:
        # "Чиста" версія - без аугментацій
        block_transform = A.NoOp()
        scene_transform = A.NoOp()
    else:
        # "Аугментована" версія - згідно з запитом
        block_transform = A.Compose([
            A.Perspective(scale=(0.02, 0.08), pad_mode=0, p=0.7),
            A.ShiftScaleRotate(shift_limit=0.1, scale_limit=(-0.2, 0.2), rotate_limit=10, p=0.8),
        ], bbox_params=A.BboxParams(format='pascal_voc', label_fields=['class_labels']))

        scene_transform = A.Compose([
            A.GaussNoise(var_limit=(10.0, 50.0), p=0.5), # Шум
            A.MotionBlur(blur_limit=(3, 15), p=0.5), # "Смуги" (stripes)
            A.RandomBrightnessContrast(brightness_limit=0.2, contrast_limit=0.2, p=0.6),
            A.Blur(blur_limit=(3, 5), p=0.3),
        ])

    return block_transform, scene_transform

# ---------------------------------
# 5. ОСНОВНА ФУНКЦІЯ ГЕНЕРАЦІЇ СЦЕНИ
# ---------------------------------

def generate_scene(fonts, is_augmented=False):
    """
    Генерує одну сцену (чисту або аугментовану)
    Повертає: (final_scene_img, final_bboxes_list)
    де final_bboxes_list = [ [class, x1, y1, x2, y2], ... ] (абсолютні координати)
    """

    # 1. Створюємо фон "сцени" (з легким шумом)
    scene_bg = np.random.randint(0, 40, SCENE_SIZE, dtype=np.uint8)

    # 2. Генеруємо "блок" з цифрами
    number_len = random.randint(1, MAX_DIGITS_IN_NUMBER)
    number_str = "".join([str(random.randint(0, 9)) for _ in range(number_len)])
    font_path = random.choice(fonts)
    font_size = random.choice(FONT_SIZES)

    block_img, bboxes = create_number_block(number_str, font_path, font_size)
    if block_img is None:
        return None, None # Не вдалося згенерувати блок

    block_h, block_w = block_img.shape
    if block_h <= 0 or block_w <= 0:
        return None, None

    # 3. Отримуємо та застосовуємо аугментації
    block_transform, scene_transform = get_transforms(is_augmented)

    class_labels = [b[0] for b in bboxes]
    pascal_bboxes = [b[1:] for b in bboxes]

    try:
        transformed = block_transform(image=block_img, bboxes=pascal_bboxes, class_labels=class_labels)
        transformed_img = transformed['image']
        transformed_bboxes = transformed['bboxes'] # Це bboxes відносно блоку
        transformed_labels = transformed['class_labels']
    except Exception as e:
        return None, None # Помилка аугментації блоку

    t_h, t_w = transformed_img.shape

    # 4. Вклеюємо "блок" на "сцену"
    max_x = SCENE_SIZE[0] - t_w
    max_y = SCENE_SIZE[1] - t_h
    if max_x <= 0 or max_y <= 0:
        return None, None # Блок завеликий

    paste_x = random.randint(0, max_x)
    paste_y = random.randint(0, max_y)

    # Вставка з маскою
    mask = (transformed_img > 0).astype(np.uint8)
    scene_bg[paste_y:paste_y+t_h, paste_x:paste_x+t_w] = np.where(
        mask > 0,
        transformed_img,
        scene_bg[paste_y:paste_y+t_h, paste_x:paste_x+t_w]
    )

    # 5. Трансформуємо "сцену"
    final_scene_img = scene_transform(image=scene_bg)['image']

    # 6. Перераховуємо bboxes в АБСОЛЮТНІ координати сцени
    final_bboxes_list = []
    for label, bbox in zip(transformed_labels, transformed_bboxes):
        # bbox - [x1, y1, x2, y2] відносно блоку
        abs_x_min = int(bbox[0] + paste_x)
        abs_y_min = int(bbox[1] + paste_y)
        abs_x_max = int(bbox[2] + paste_x)
        abs_y_max = int(bbox[3] + paste_y)

        # Перевірка, чи bbox не виліз за межі (особливо важливо для "чистих" версій)
        if abs_x_max < SCENE_SIZE[0] and abs_y_max < SCENE_SIZE[1] and \
           abs_x_min > 0 and abs_y_min > 0 and \
           (abs_x_max - abs_x_min) > 1 and (abs_y_max - abs_y_min) > 1:

            final_bboxes_list.append([label, abs_x_min, abs_y_min, abs_x_max, abs_y_max])

    if not final_bboxes_list:
        return None, None

    return final_scene_img, final_bboxes_list

# ---------------------------------
# 6. ГОЛОВНИЙ ЦИКЛ ГЕНЕРАЦІЇ
# ---------------------------------
print("--- Етап 3: Запуск Мега-Генерації ---")

try:
    train_fonts = get_font_files(FONT_DIR)
    valid_fonts = get_font_files(VALID_FONT_DIR)
    if not train_fonts or not valid_fonts:
        raise FileNotFoundError("Шрифти не знайдено!")

    # Визначаємо, які індекси йдуть у train, а які у valid
    indices = list(range(NUM_BASE_IMAGES))
    random.shuffle(indices)
    split_point = int(NUM_BASE_IMAGES * TRAIN_SPLIT_RATIO)
    train_indices = indices[:split_point]
    valid_indices = indices[split_point:]

    print(f"Буде згенеровано {NUM_BASE_IMAGES} базових наборів (x2 = {NUM_BASE_IMAGES*2} всього):")
    print(f"Train: {len(train_indices)} наборів ({len(train_indices)*2} зображень)")
    print(f"Valid: {len(valid_indices)} наборів ({len(valid_indices)*2} зображень)")

    global_classifier_counter = 0

    # Створюємо один progress bar
    pbar = tqdm(total=NUM_BASE_IMAGES, desc="Мега-генерація")

    for i in range(NUM_BASE_IMAGES):

        # 1. Визначаємо, куди зберігати (train чи valid)
        if i in train_indices:
            yolo_img_dir = YOLO_TRAIN_IMG
            yolo_lbl_dir = YOLO_TRAIN_LBL
            class_save_dir = CLASS_TRAIN_DIR
            fonts = train_fonts
        else:
            yolo_img_dir = YOLO_VALID_IMG
            yolo_lbl_dir = YOLO_VALID_LBL
            class_save_dir = CLASS_VALID_DIR
            fonts = valid_fonts

        base_img_name = f"img_{i:06d}" # 000001, 000002...

        # 2. Генеруємо обидві версії (чисту та аугментовану)
        versions_to_generate = [
            {"is_augmented": False, "suffix": "clean"},
            {"is_augmented": True, "suffix": "aug"}
        ]

        for config in versions_to_generate:
            is_augmented = config["is_augmented"]
            suffix = config["suffix"]

            # Генеруємо сцену
            scene_img, bboxes_list = None, None
            while scene_img is None: # Повторюємо, якщо генерація не вдалася
                scene_img, bboxes_list = generate_scene(fonts, is_augmented=is_augmented)

            # Формуємо ім'я файлу
            current_img_name = f"{base_img_name}_{suffix}.png"
            current_lbl_name = f"{base_img_name}_{suffix}.txt"

            # --- ЗБЕРІГАЄМО ДЛЯ YOLO ---
            yolo_img_path = os.path.join(yolo_img_dir, current_img_name)
            yolo_lbl_path = os.path.join(yolo_lbl_dir, current_lbl_name)

            # Зберігаємо зображення
            Image.fromarray(scene_img).save(yolo_img_path)

            # Готуємо та зберігаємо .txt для YOLO
            yolo_labels_txt = []
            for bbox_data in bboxes_list:
                label, x1, y1, x2, y2 = bbox_data

                # Конвертуємо у YOLO формат (class, x_center, y_center, width, height)
                x_center = (x1 + x2) / 2 / SCENE_SIZE[0]
                y_center = (y1 + y2) / 2 / SCENE_SIZE[1]
                width = (x2 - x1) / SCENE_SIZE[0]
                height = (y2 - y1) / SCENE_SIZE[1]

                yolo_labels_txt.append(f"{label} {x_center:.6f} {y_center:.6f} {width:.6f} {height:.6f}")

            with open(yolo_lbl_path, 'w') as f:
                f.write("\n".join(yolo_labels_txt))

            # --- ЗБЕРІГАЄМО ДЛЯ КЛАСИФІКАТОРА ---
            for bbox_data in bboxes_list:
                label, x1, y1, x2, y2 = bbox_data

                # 1. Вирізаємо цифру з 640x640 сцени
                cropped_digit = scene_img[y1:y2, x1:x2]

                # 2. Обробляємо (масштабуємо до 64x64)
                final_64x64_image = preprocess_for_classifier(cropped_digit)

                if final_64x64_image is not None:
                    # 3. Зберігаємо
                    class_label_dir = os.path.join(class_save_dir, str(int(label)))
                    img_name = f"digit_{global_classifier_counter:08d}.png"
                    save_path = os.path.join(class_label_dir, img_name)

                    Image.fromarray(final_64x64_image).save(save_path)
                    global_classifier_counter += 1

        pbar.update(1) # Оновлюємо прогрес-бар

    pbar.close()
    print(f"\n--- ✅ УСЮ ГЕНЕРАЦІЮ ЗАВЕРШЕНО! ---")
    print(f"Дані для YOLO збережено в: {YOLO_DIR}")
    print(f"Дані для Класифікатора збережено в: {CLASSIFIER_DIR}")
    print(f"Всього згенеровано {global_classifier_counter} зображень для класифікатора.")

except Exception as e:
    print(f"\n\n--- ❌ ПОМИЛКА ПІД ЧАС ВИКОНАННЯ ---")
    print(e)
    import traceback
    traceback.print_exc()

--- Етап 1: Мега-конфігурація ---
Очищення старих директорій...
Створення нових директорій...
Структуру директорій створено.
--- Етап 3: Запуск Мега-Генерації ---
Буде згенеровано 55000 базових наборів (x2 = 110000 всього):
Train: 38500 наборів (77000 зображень)
Valid: 16500 наборів (33000 зображень)



Мега-генерація:   0%|                                                                         | 0/55000 [04:56<?, ?it/s]
/tmp/ipykernel_508/2423395069.py:163: UserWarning: Argument(s) 'pad_mode' are not valid for transform Perspective
  A.Perspective(scale=(0.02, 0.08), pad_mode=0, p=0.7),
/tmp/ipykernel_508/2423395069.py:168: UserWarning: Argument(s) 'var_limit' are not valid for transform GaussNoise
  A.GaussNoise(var_limit=(10.0, 50.0), p=0.5), # Шум

Мега-генерація: 100%|███████████████████████████████████████████████████████████| 55000/55000 [2:02:27<00:00,  7.49it/s]


--- ✅ УСЮ ГЕНЕРАЦІЮ ЗАВЕРШЕНО! ---
Дані для YOLO збережено в: learning/data_yolo_mega
Дані для Класифікатора збережено в: learning/data_classifier_mega
Всього згенеровано 329803 зображень для класифікатора.
